Hi, this is my final. I have tried different project, however, I have decided to work on car plate recognition. The reason is that I want to learn computer vision. Honestly, I have not finished it yet. I will work on it, will try to finish it and get final product, for now I will send what I have done. Thanks for your attention.

As tutorial I have used that link 
https://towardsdatascience.com/ai-based-indian-license-plate-detector-de9d48ca8951

Importing libraries

In [1]:
import cv2

In [2]:
import numpy as np

In [3]:
import pandas as pd

In [4]:
from keras.models import Sequential

Using TensorFlow backend.


In [5]:
from keras.layers import Dense

In [6]:
from keras.layers import Dropout

In [7]:
from keras.layers import Flatten, MaxPool2D

In [8]:
from keras.layers.convolutional import Conv2D

In [9]:
from keras.layers.convolutional import MaxPooling2D

In [10]:
from keras import backend as K

In [11]:
from keras.utils import np_utils

In [12]:
from sklearn.model_selection import train_test_split

Number plate detection:

In [13]:
def extract_plate(img): # the function detects and perfors blurring on the number plate.
	plate_img = img.copy()
	
	#Loads the data required for detecting the license plates from cascade classifier.
	plate_cascade = cv2.CascadeClassifier('./indian_license_plate.xml')

	# detects numberplates and returns the coordinates and dimensions of detected license plate's contours.
	plate_rect = plate_cascade.detectMultiScale(plate_img, scaleFactor = 1.3, minNeighbors = 7)

	for (x,y,w,h) in plate_rect:
		a,b = (int(0.02*img.shape[0]), int(0.025*img.shape[1])) #parameter tuning
		plate = plate_img[y+a:y+h-a, x+b:x+w-b, :]
		# finally representing the detected contours by drawing rectangles around the edges.
		cv2.rectangle(plate_img, (x,y), (x+w, y+h), (51,51,255), 3)
        
	return plate_img, plate # returning the processed image

In [14]:
# Find characters in the resulting images
def segment_characters(image) :

    # Preprocess cropped license plate image
    img = cv2.resize(image, (333, 75))
    img_gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    _, img_binary = cv2.threshold(img_gray, 200, 255, cv2.THRESH_BINARY+cv2.THRESH_OTSU)
    img_erode = cv2.erode(img_binary, (3,3))
    img_dilate = cv2.dilate(img_erode, (3,3))

    LP_WIDTH = img_dilate.shape[0]
    LP_HEIGHT = img_dilate.shape[1]

    # Make borders white
    img_dilate[0:3,:] = 255
    img_dilate[:,0:3] = 255
    img_dilate[72:75,:] = 255
    img_dilate[:,330:333] = 255

    # Estimations of character contours sizes of cropped license plates
    dimensions = [LP_WIDTH/6, LP_WIDTH/2, LP_HEIGHT/10, 2*LP_HEIGHT/3]

    # Get contours within cropped license plate
    char_list = find_contours(dimensions, img_dilate)

    return char_list

Image processing

The alphanumeric characters from the license plate.

In [15]:
# Match contours to license plate or character template
def find_contours(dimensions, img) :

    # Find all contours in the image
    cntrs, _ = cv2.findContours(img.copy(), cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)

    # Retrieve potential dimensions
    lower_width = dimensions[0]
    upper_width = dimensions[1]
    lower_height = dimensions[2]
    upper_height = dimensions[3]
    

    # Check largest 5 or  15 contours for license plate or character respectively
    cntrs = sorted(cntrs, key=cv2.contourArea, reverse=True)[:15]

    x_cntr_list = []
    target_contours = []
    img_res = []
    for cntr in cntrs :
        #detects contour in binary image and returns the coordinates of rectangle enclosing it
        intX, intY, intWidth, intHeight = cv2.boundingRect(cntr)
        
        #checking the dimensions of the contour to filter out the characters by contour's size
        if intWidth > lower_width and intWidth < upper_width and intHeight > lower_height and intHeight < upper_height :
            x_cntr_list.append(intX) #stores the x coordinate of the character's contour, to used later for indexing the contours

            char_copy = np.zeros((44,24))
            #extracting each character using the enclosing rectangle's coordinates.
            char = img[intY:intY+intHeight, intX:intX+intWidth]
            char = cv2.resize(char, (20, 40))

            # Make result formatted for classification: invert colors
            char = cv2.subtract(255, char)

            # Resize the image to 24x44 with black border
            char_copy[2:42, 2:22] = char
            char_copy[0:2, :] = 0
            char_copy[:, 0:2] = 0
            char_copy[42:44, :] = 0
            char_copy[:, 22:24] = 0

            img_res.append(char_copy) #List that stores the character's binary image (unsorted)

    #Return characters on ascending order with respect to the x-coordinate (most-left character first)
    
    #arbitrary function that stores sorted list of character indeces
    indices = sorted(range(len(x_cntr_list)), key=lambda k: x_cntr_list[k])
    img_res_copy = []
    for idx in indices:
        img_res_copy.append(img_res[idx])# stores character images according to their index
    img_res = np.array(img_res_copy)

In [16]:
model = Sequential()

In [17]:
model.add(Conv2D(filters=32, kernel_size=(5,5), input_shape=(28, 28, 1), activation='relu'))

In [18]:
model.add(MaxPooling2D(pool_size=(2, 2)))

In [19]:
from keras.layers import MaxPooling2D

In [20]:
model.add(MaxPooling2D(pool_size=(2, 2)))

In [21]:
model.add(Dropout(rate=0.4))

In [22]:
model.add(Flatten())

In [23]:
model.add(Dense(units=128, activation='relu'))

In [31]:
model.add(Dense(units=36, activation='softmax'))

In [32]:
data = pd.read_csv('image_data.csv') #reading the csv file

In [33]:
data.head()

Unnamed: 0   p1   p2   p3   p4   p5   p6   p7   p8   p9 ...  p776  p777  \
0           0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0 ...   0.0   0.0   
1           1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0 ...   0.0   0.0   
2           2  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0 ...   0.0   0.0   
3           3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0 ...   0.0   0.0   
4           4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0 ...   0.0   0.0   

   p778  p779  p780  p781  p782  p783  p784  y  
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  1  
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0  1  
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0  1  
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0  1  
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0  1  

[5 rows x 786 columns]

In [34]:
X = []
Y = data['y'] #storing the labels in Y
del data['y'] #deleting the column 'y'

In [35]:
data.head()

Unnamed: 0   p1   p2   p3   p4   p5   p6   p7   p8   p9  ...   p775  p776  \
0           0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0   0.0   
1           1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0   0.0   
2           2  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0   0.0   
3           3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0   0.0   
4           4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...    0.0   0.0   

   p777  p778  p779  p780  p781  p782  p783  p784  
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  

[5 rows x 785 columns]

In [36]:
for i in range(data.shape[0]): #iterating over all the rows.
    flat_pixels = data.iloc[i].values[1:] #extracting pixel values
    image = np.reshape(flat_pixels, (28,28)) #reshaping to 28x28p
    X.append(image) #adding to input feature list

In [40]:
import random

In [67]:
# split the data into training (70%) and testing (30%)
(X_train, X_test, Y_train, Y_test) = train_test_split(X, Y, test_size=0.30, random_state=np.random)



In [69]:
# one hot encode outputs
Y_train = np_utils.to_categorical(Y_train)
Y_test = np_utils.to_categorical(Y_test)


In [72]:
type(X_train)

list

In [73]:
X_train

[array([[0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        ],
        [0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        , 0.        , 0.        ,
         0.        , 0.        , 0.        ],
        [0.        , 0.6122449 , 0.85714286, 0.85714286, 0.85714286,
         0.85714286, 0.85714286, 0.85714286, 0.85714286, 0.85714286,
         0.85714286, 0.85714286, 0.85714286, 0.85714286, 0.85714286,
         0.

In [76]:
import numpy as np

In [81]:
X_train=np.array(X_train)

In [82]:
X_train = X_train.reshape(-1,28,28,1)

In [83]:
X_test=np.array(X_test)
X_test = X_test.reshape(-1,28,28,1)

In [85]:
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
#performing fit


Continue